# Eat Safe, Love

## Part 1: Database and Jupyter Notebook Set Up

Import the data provided in the `establishments.json` file from your Terminal. Name the database `uk_food` and the collection `establishments`.

Within this markdown cell, copy the line of text you used to import the data from your Terminal. This way, future analysts will be able to repeat your process.

e.g.: Import the dataset with `YOUR IMPORT TEXT HERE`

In [157]:
# Import dependencies
from pymongo import MongoClient
from pprint import pprint
from bson.decimal128 import Decimal128

In [158]:
# Create an instance of MongoClient
mongo = MongoClient(port=27017)

In [159]:
# confirm that our new database was created
print(mongo.list_database_names())

['admin', 'config', 'local', 'uk_food']


In [160]:
# assign the uk_food database to a variable name
db = mongo['uk_food']

In [161]:
# review the collections in our new database
print(db.list_collection_names())

['establishments']


In [162]:
# review a document in the establishments collection
pprint(db.establishments.find_one())

{'AddressLine1': 'East Cliff Pavilion',
 'AddressLine2': 'Wear Bay Road',
 'AddressLine3': 'Folkestone',
 'AddressLine4': 'Kent',
 'BusinessName': 'The Pavilion',
 'BusinessType': 'Restaurant/Cafe/Canteen',
 'BusinessTypeID': 1,
 'ChangesByServerID': 0,
 'Distance': 4591.765489457773,
 'FHRSID': 1043695,
 'LocalAuthorityBusinessID': 'PI/000073616',
 'LocalAuthorityCode': '188',
 'LocalAuthorityEmailAddress': 'foodteam@folkestone-hythe.gov.uk',
 'LocalAuthorityName': 'Folkestone and Hythe',
 'LocalAuthorityWebSite': 'http://www.folkestone-hythe.gov.uk',
 'NewRatingPending': False,
 'Phone': '',
 'PostCode': 'CT19 6BL',
 'RatingDate': '2018-04-04T00:00:00',
 'RatingKey': 'fhrs_5_en-gb',
 'RatingValue': 5,
 'RightToReply': '',
 'SchemeType': 'FHRS',
 '_id': ObjectId('664ccb3093ec43176e28d2a5'),
 'geocode': {'latitude': 51.083812, 'longitude': 1.195625},
 'links': [{'href': 'https://api.ratings.food.gov.uk/establishments/1043695',
            'rel': 'self'}],
 'meta': {'dataSource': None,


In [163]:
# assign the collection to a variable
establishments = db['establishments']

## Part 2: Update the Database

1. An exciting new halal restaurant just opened in Greenwich, but hasn't been rated yet. The magazine has asked you to include it in your analysis. Add the following restaurant "Penang Flavours" to the database.

In [164]:
# Create a dictionary for the new restaurant data
new_restaurant = {
    "BusinessName":"Penang Flavours",
    "BusinessType":"Restaurant/Cafe/Canteen",
    "BusinessTypeID":"",
    "AddressLine1":"Penang Flavours",
    "AddressLine2":"146A Plumstead Rd",
    "AddressLine3":"London",
    "AddressLine4":"",
    "PostCode":"SE18 7DY",
    "Phone":"",
    "LocalAuthorityCode":"511",
    "LocalAuthorityName":"Greenwich",
    "LocalAuthorityWebSite":"http://www.royalgreenwich.gov.uk",
    "LocalAuthorityEmailAddress":"health@royalgreenwich.gov.uk",
    "scores":{
        "Hygiene":"",
        "Structural":"",
        "ConfidenceInManagement":""
    },
    "SchemeType":"FHRS",
    "geocode":{
        "longitude":"0.08384000",
        "latitude":"51.49014200"
    },
    "RightToReply":"",
    "Distance":4623.9723280747176,
    "NewRatingPending":True
}

In [165]:
# Insert the new restaurant into the collection
establishments.insert_one(new_restaurant)

InsertOneResult(ObjectId('664e8444ba6e3c3a929d889a'), acknowledged=True)

In [166]:
# Check that the new restaurant was inserted
query = {'BusinessName': 'Penang Flavours'}
results = establishments.find(query)
for result in results:
    pprint(result)

{'AddressLine1': 'Penang Flavours',
 'AddressLine2': '146A Plumstead Rd',
 'AddressLine3': 'London',
 'AddressLine4': '',
 'BusinessName': 'Penang Flavours',
 'BusinessType': 'Restaurant/Cafe/Canteen',
 'BusinessTypeID': 1,
 'Distance': 4623.972328074718,
 'LocalAuthorityCode': '511',
 'LocalAuthorityEmailAddress': 'health@royalgreenwich.gov.uk',
 'LocalAuthorityName': 'Greenwich',
 'LocalAuthorityWebSite': 'http://www.royalgreenwich.gov.uk',
 'NewRatingPending': True,
 'Phone': '',
 'PostCode': 'SE18 7DY',
 'RightToReply': '',
 'SchemeType': 'FHRS',
 '_id': ObjectId('664ccb3dba6e3c3a929d8898'),
 'geocode': {'latitude': 51.490142, 'longitude': 0.08384},
 'scores': {'ConfidenceInManagement': '', 'Hygiene': '', 'Structural': ''}}
{'AddressLine1': 'Penang Flavours',
 'AddressLine2': '146A Plumstead Rd',
 'AddressLine3': 'London',
 'AddressLine4': '',
 'BusinessName': 'Penang Flavours',
 'BusinessType': 'Restaurant/Cafe/Canteen',
 'BusinessTypeID': '',
 'Distance': 4623.972328074718,
 'Loc

2. Find the BusinessTypeID for "Restaurant/Cafe/Canteen" and return only the `BusinessTypeID` and `BusinessType` fields.

In [167]:
# Find the BusinessTypeID for "Restaurant/Cafe/Canteen" and return only the BusinessTypeID and BusinessType fields
# Define the query
query = {'BusinessType': 'Restaurant/Cafe/Canteen'}

# Define the projection to return only BusinessTypeID and BusinessType fields
fields = {'_id': 0, 'BusinessTypeID': 1, 'BusinessType': 1}

# Execute the query
result = db.establishments.find_one(query, fields)

# Pretty print the result
pprint(result)

{'BusinessType': 'Restaurant/Cafe/Canteen', 'BusinessTypeID': 1}


In [168]:
bu_id = result['BusinessTypeID']
bu_id

1

3. Update the new restaurant with the `BusinessTypeID` you found.

In [169]:
# Update the new restaurant with the correct BusinessTypeID
update_query = {"BusinessName": "Penang Flavours"}
update_operation = {"$set": {"BusinessTypeID": bu_id}}
update_result = db.establishments.update_one(update_query, update_operation)

In [170]:
# Confirm that the new restaurant was updated
query = {"BusinessName": "Penang Flavours"}

# Define the projection to return only BusinessTypeID and BusinessType fields
fields = {'_id': 0, 'BusinessName': 1, 'BusinessTypeID': 1}

# Execute the query
result = db.establishments.find_one(query, fields)

# Pretty print the result
pprint(result)

{'BusinessName': 'Penang Flavours', 'BusinessTypeID': 1}


4. The magazine is not interested in any establishments in Dover, so check how many documents contain the Dover Local Authority. Then, remove any establishments within the Dover Local Authority from the database, and check the number of documents to ensure they were deleted.

In [171]:
# Find how many documents have LocalAuthorityName as "Dover"
query = {'LocalAuthorityName': 'Dover'}
results = establishments.find(query)
for result in results:
    pprint(result)

In [172]:
# count of establishments having LocalAuthorityName as "Dover"
query = {'LocalAuthorityName': 'Dover'}
results = establishments.count_documents(query)
results

0

In [173]:
# Delete all documents where LocalAuthorityName is "Dover"
delete_query = {'LocalAuthorityName': 'Dover'}

# Delete all matching documents
delete_result = db.establishments.delete_many(delete_query)

In [174]:
# Check if any remaining documents include Dover
query = {'LocalAuthorityName': 'Dover'}
results = establishments.count_documents(query)
results

0

In [175]:
# Check that other documents remain with 'find_one'
# Define a query to find a document where LocalAuthorityName is not equal to "Dover"
query = {'LocalAuthorityName': {'$ne': 'Dover'}}

# Find one document that matches the query
remaining_document = db.establishments.find_one(query)

# Print the remaining document
pprint(remaining_document)

{'AddressLine1': 'East Cliff Pavilion',
 'AddressLine2': 'Wear Bay Road',
 'AddressLine3': 'Folkestone',
 'AddressLine4': 'Kent',
 'BusinessName': 'The Pavilion',
 'BusinessType': 'Restaurant/Cafe/Canteen',
 'BusinessTypeID': 1,
 'ChangesByServerID': 0,
 'Distance': 4591.765489457773,
 'FHRSID': 1043695,
 'LocalAuthorityBusinessID': 'PI/000073616',
 'LocalAuthorityCode': '188',
 'LocalAuthorityEmailAddress': 'foodteam@folkestone-hythe.gov.uk',
 'LocalAuthorityName': 'Folkestone and Hythe',
 'LocalAuthorityWebSite': 'http://www.folkestone-hythe.gov.uk',
 'NewRatingPending': False,
 'Phone': '',
 'PostCode': 'CT19 6BL',
 'RatingDate': '2018-04-04T00:00:00',
 'RatingKey': 'fhrs_5_en-gb',
 'RatingValue': 5,
 'RightToReply': '',
 'SchemeType': 'FHRS',
 '_id': ObjectId('664ccb3093ec43176e28d2a5'),
 'geocode': {'latitude': 51.083812, 'longitude': 1.195625},
 'links': [{'href': 'https://api.ratings.food.gov.uk/establishments/1043695',
            'rel': 'self'}],
 'meta': {'dataSource': None,


5. Some of the number values are stored as strings, when they should be stored as numbers.

Use `update_many` to convert `latitude` and `longitude` to decimal numbers.

In [176]:
# Change the data type from String to Decimal for longitude and latitude

for document in establishments.find({}):
    if 'geocode' in document:
        updates = {}
        if 'latitude' in document['geocode'] and isinstance(document['geocode']['latitude'], str):
            updates['geocode.latitude'] = float(document['geocode']['latitude'])
        if 'longitude' in document['geocode'] and isinstance(document['geocode']['longitude'], str):
            updates['geocode.longitude'] = float(document['geocode']['longitude'])
        
        if updates:
            establishments.update_one({'_id': document['_id']}, {'$set': updates})

print("Conversion to decimal numbers completed.")

Conversion to decimal numbers completed.


In [177]:
# check one document
pprint(db.establishments.find_one())

{'AddressLine1': 'East Cliff Pavilion',
 'AddressLine2': 'Wear Bay Road',
 'AddressLine3': 'Folkestone',
 'AddressLine4': 'Kent',
 'BusinessName': 'The Pavilion',
 'BusinessType': 'Restaurant/Cafe/Canteen',
 'BusinessTypeID': 1,
 'ChangesByServerID': 0,
 'Distance': 4591.765489457773,
 'FHRSID': 1043695,
 'LocalAuthorityBusinessID': 'PI/000073616',
 'LocalAuthorityCode': '188',
 'LocalAuthorityEmailAddress': 'foodteam@folkestone-hythe.gov.uk',
 'LocalAuthorityName': 'Folkestone and Hythe',
 'LocalAuthorityWebSite': 'http://www.folkestone-hythe.gov.uk',
 'NewRatingPending': False,
 'Phone': '',
 'PostCode': 'CT19 6BL',
 'RatingDate': '2018-04-04T00:00:00',
 'RatingKey': 'fhrs_5_en-gb',
 'RatingValue': 5,
 'RightToReply': '',
 'SchemeType': 'FHRS',
 '_id': ObjectId('664ccb3093ec43176e28d2a5'),
 'geocode': {'latitude': 51.083812, 'longitude': 1.195625},
 'links': [{'href': 'https://api.ratings.food.gov.uk/establishments/1043695',
            'rel': 'self'}],
 'meta': {'dataSource': None,


Use `update_many` to convert `RatingValue` to integer numbers.

In [178]:
# Set non 1-5 Rating Values to Null
non_ratings = ["AwaitingInspection", "Awaiting Inspection", "AwaitingPublication", "Pass", "Exempt"]
establishments.update_many({"RatingValue": {"$in": non_ratings}}, [ {'$set':{ "RatingValue" : None}} ])

UpdateResult({'n': 0, 'nModified': 0, 'ok': 1.0, 'updatedExisting': False}, acknowledged=True)

In [179]:
# Change the data type from String to Integer for RatingValue
for document in establishments.find({}):
    if 'RatingValue' in document and document['RatingValue'] is not None:
        try:
            rating_value_int = int(document['RatingValue'])
            establishments.update_one(
                {'_id': document['_id']},
                {'$set': {'RatingValue': rating_value_int}}
            )
            print(f"Updated document ID: {document['_id']} with RatingValue: {rating_value_int}")
        except ValueError:
            print(f"Could not convert RatingValue for document ID: {document['_id']}")


Updated document ID: 664ccb3093ec43176e28d2a5 with RatingValue: 5
Updated document ID: 664ccb3093ec43176e28d2a6 with RatingValue: 5
Updated document ID: 664ccb3093ec43176e28d2a7 with RatingValue: 4
Updated document ID: 664ccb3093ec43176e28d2a9 with RatingValue: 5
Updated document ID: 664ccb3093ec43176e28d2aa with RatingValue: 5
Updated document ID: 664ccb3093ec43176e28d2ac with RatingValue: 5
Updated document ID: 664ccb3093ec43176e28d2ad with RatingValue: 5
Updated document ID: 664ccb3093ec43176e28d2ae with RatingValue: 5
Updated document ID: 664ccb3093ec43176e28d2af with RatingValue: 5
Updated document ID: 664ccb3093ec43176e28d2b0 with RatingValue: 4
Updated document ID: 664ccb3093ec43176e28d2b1 with RatingValue: 5
Updated document ID: 664ccb3093ec43176e28d2b2 with RatingValue: 5
Updated document ID: 664ccb3093ec43176e28d2b3 with RatingValue: 5
Updated document ID: 664ccb3093ec43176e28d2b4 with RatingValue: 5
Updated document ID: 664ccb3093ec43176e28d2b5 with RatingValue: 4
Updated do

In [180]:
pprint(db.establishments.find_one())

{'AddressLine1': 'East Cliff Pavilion',
 'AddressLine2': 'Wear Bay Road',
 'AddressLine3': 'Folkestone',
 'AddressLine4': 'Kent',
 'BusinessName': 'The Pavilion',
 'BusinessType': 'Restaurant/Cafe/Canteen',
 'BusinessTypeID': 1,
 'ChangesByServerID': 0,
 'Distance': 4591.765489457773,
 'FHRSID': 1043695,
 'LocalAuthorityBusinessID': 'PI/000073616',
 'LocalAuthorityCode': '188',
 'LocalAuthorityEmailAddress': 'foodteam@folkestone-hythe.gov.uk',
 'LocalAuthorityName': 'Folkestone and Hythe',
 'LocalAuthorityWebSite': 'http://www.folkestone-hythe.gov.uk',
 'NewRatingPending': False,
 'Phone': '',
 'PostCode': 'CT19 6BL',
 'RatingDate': '2018-04-04T00:00:00',
 'RatingKey': 'fhrs_5_en-gb',
 'RatingValue': 5,
 'RightToReply': '',
 'SchemeType': 'FHRS',
 '_id': ObjectId('664ccb3093ec43176e28d2a5'),
 'geocode': {'latitude': 51.083812, 'longitude': 1.195625},
 'links': [{'href': 'https://api.ratings.food.gov.uk/establishments/1043695',
            'rel': 'self'}],
 'meta': {'dataSource': None,


In [181]:
# Check that the coordinates and rating value are now numbers

# Find all documents in the establishments
documents = establishments.find({})

# Iterate over each document and print the data types of latitude and longitude
for document in documents:
    latitude_type = type(document['geocode']['latitude']) if 'geocode' in document and 'latitude' in document['geocode'] else None
    longitude_type = type(document['geocode']['longitude']) if 'geocode' in document and 'longitude' in document['geocode'] else None
    ratingValue_type = type(document['RatingValue']) if 'RatingValue' in document else None

    print(f"Latitude_type: {latitude_type}; Longitude type: {longitude_type}; RatingValue type: {ratingValue_type}")
    print("---------")

Latitude_type: <class 'float'>; Longitude type: <class 'float'>; RatingValue type: <class 'int'>
---------
Latitude_type: <class 'float'>; Longitude type: <class 'float'>; RatingValue type: <class 'int'>
---------
Latitude_type: <class 'float'>; Longitude type: <class 'float'>; RatingValue type: <class 'int'>
---------
Latitude_type: <class 'float'>; Longitude type: <class 'float'>; RatingValue type: <class 'int'>
---------
Latitude_type: <class 'float'>; Longitude type: <class 'float'>; RatingValue type: <class 'int'>
---------
Latitude_type: <class 'float'>; Longitude type: <class 'float'>; RatingValue type: <class 'int'>
---------
Latitude_type: <class 'float'>; Longitude type: <class 'float'>; RatingValue type: <class 'int'>
---------
Latitude_type: <class 'float'>; Longitude type: <class 'float'>; RatingValue type: <class 'int'>
---------
Latitude_type: <class 'float'>; Longitude type: <class 'float'>; RatingValue type: <class 'int'>
---------
Latitude_type: <class 'float'>; Longi

In [182]:
# close client connection
mongo.close()